## **PART 1: Data Ingestion and Preparation**

In [0]:
# Read files in Databricks from Azure Blob Storage and make a copy to DBFS
storage_account_name = 'your_storage_account_name'
storage_account_access_key = 'your_storage_account_access_key'
blob_container_name = 'your_container_name'

In [0]:
dbutils.fs.mount(
    source = f'wasbs://{blob_container_name}@{storage_account_name}.blob.core.windows.net',
     mount_point = "/mnt/taxidata",
    extra_configs = {f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net": storage_account_access_key}
)

Out[11]: True

Move Green Taxi files and Yellow Taxi files into seperate folders

In [0]:
# Move Green Taxi files and Yellow Taxi files into seperate folders
## Create directories
dbutils.fs.mkdirs('/dbfs/taxidata/yellowtaxi')
dbutils.fs.mkdirs('/dbfs/taxidata/greentaxi')

Out[12]: True

In [0]:
## Copy yellow taxi files
dbutils.fs.cp('/mnt/taxidata/yellow_taxi_2015.parquet', '/dbfs/taxidata/yellowtaxi/yellow_taxi_2015.parquet')
dbutils.fs.cp('/mnt/taxidata/yellow_taxi_2016.parquet', '/dbfs/taxidata/yellowtaxi/yellow_taxi_2016.parquet')
dbutils.fs.cp('/mnt/taxidata/yellow_taxi_2017.parquet', '/dbfs/taxidata/yellowtaxi/yellow_taxi_2017.parquet')
dbutils.fs.cp('/mnt/taxidata/yellow_taxi_2018.parquet', '/dbfs/taxidata/yellowtaxi/yellow_taxi_2018.parquet')
dbutils.fs.cp('/mnt/taxidata/yellow_taxi_2019.parquet', '/dbfs/taxidata/yellowtaxi/yellow_taxi_2019.parquet')
dbutils.fs.cp('/mnt/taxidata/yellow_taxi_2020.parquet', '/dbfs/taxidata/yellowtaxi/yellow_taxi_2020.parquet')
dbutils.fs.cp('/mnt/taxidata/yellow_taxi_2021.parquet', '/dbfs/taxidata/yellowtaxi/yellow_taxi_2021.parquet')
dbutils.fs.cp('/mnt/taxidata/yellow_taxi_2022.parquet', '/dbfs/taxidata/yellowtaxi/yellow_taxi_2022.parquet')

## Copy green taxi files
dbutils.fs.cp('/mnt/taxidata/green_taxi_2015.parquet', '/dbfs/taxidata/greentaxi/green_taxi_2015.parquet')
dbutils.fs.cp('/mnt/taxidata/green_taxi_2016.parquet', '/dbfs/taxidata/greentaxi/green_taxi_2016.parquet')
dbutils.fs.cp('/mnt/taxidata/green_taxi_2017.parquet', '/dbfs/taxidata/greentaxi/green_taxi_2017.parquet')
dbutils.fs.cp('/mnt/taxidata/green_taxi_2018.parquet', '/dbfs/taxidata/greentaxi/green_taxi_2018.parquet')
dbutils.fs.cp('/mnt/taxidata/green_taxi_2019.parquet', '/dbfs/taxidata/greentaxi/green_taxi_2019.parquet')
dbutils.fs.cp('/mnt/taxidata/green_taxi_2020.parquet', '/dbfs/taxidata/greentaxi/green_taxi_2020.parquet')
dbutils.fs.cp('/mnt/taxidata/green_taxi_2021.parquet', '/dbfs/taxidata/greentaxi/green_taxi_2021.parquet')
dbutils.fs.cp('/mnt/taxidata/green_taxi_2022.parquet', '/dbfs/taxidata/greentaxi/green_taxi_2022.parquet')


Out[13]: True

In [0]:
# Read dataframe
df_yellow = spark.read.parquet('/dbfs/taxidata/yellowtaxi')

In [0]:
# Read dataframe
df_green = spark.read.parquet('/dbfs/taxidata/greentaxi')

In [0]:
# Count the numbers of records for yellow taxi
yellow_taxi_count = df_yellow.count()
print(f"Yellow taxi: {yellow_taxi_count}")

Yellow taxi: 663055251


In [0]:
# Count the numbers of records for green taxi
green_taxi_count = df_green.count()
print(f"Green taxi: {green_taxi_count}")

Green taxi: 66200401


In [0]:
# Read taxi_zone_lookup csv file 
taxi_zone_lookup = spark.read.option("header", "true").csv("/mnt/taxidata/taxi_zone_lookup.csv")

### Explore the dataset

In [0]:
# Import packages
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql.functions import col
from pyspark.sql.functions import to_timestamp

In [0]:
# Create a Spark Session
spark = SparkSession.builder.appName('Taxi data processing').getOrCreate()

In [0]:
# Convert pickup and dropoff datetime columns from string to timestamp
df_green = df_green.withColumn('lpep_pickup_timestamp', to_timestamp(col('lpep_pickup_datetime'), 'yyyy-MM-dd HH:mm:ss'))
df_green = df_green.withColumn('lpep_dropoff_timestamp', to_timestamp(col('lpep_dropoff_datetime'), 'yyyy-MM-dd HH:mm:ss'))

df_yellow = df_yellow.withColumn('tpep_pickup_timestamp', to_timestamp(col('tpep_pickup_datetime'), 'yyyy-MM-dd HH:mm:ss'))
df_yellow = df_yellow.withColumn('tpep_dropoff_timestamp', to_timestamp(col('tpep_dropoff_datetime'), 'yyyy-MM-dd HH:mm:ss'))

Remove trips finishing before starting time

In [0]:
# df_green
df_green = df_green.filter(df_green['lpep_dropoff_datetime'] >= df_green['lpep_pickup_datetime'])

# df_yellow
df_yellow = df_yellow.filter(df_yellow['tpep_dropoff_datetime'] >= df_yellow['tpep_pickup_datetime'])

Remove trips where the pickup/dropoff datetime is outside of the range

In [0]:
# Define the valid datetime range
valid_start_date = '2015-01-01T00:00:00.000+00:00'
valid_end_date = '2022-12-31T23:59:59.999+00:00'

In [0]:
# df_green 
df_green = df_green.filter((col('lpep_pickup_timestamp') >= valid_start_date) & (col('lpep_pickup_timestamp') <= valid_end_date) &
                           (col('lpep_dropoff_timestamp') >= valid_start_date) & (col('lpep_dropoff_timestamp') <= valid_end_date))

# df_yellow
df_yellow = df_yellow.filter((col('tpep_pickup_timestamp') >= valid_start_date) & (col('tpep_pickup_timestamp') <= valid_end_date) &
                             (col('tpep_dropoff_timestamp') >= valid_start_date) & (col('tpep_dropoff_timestamp') <= valid_end_date))

Remove trips with negative speed

In [0]:
# Import unix_timestamp package
from pyspark.sql.functions import unix_timestamp

In [0]:
# Calculate trip duration
## df_green
df_green = df_green.withColumn('trip_duration', (unix_timestamp(col('lpep_dropoff_timestamp')) - unix_timestamp(col('lpep_pickup_timestamp'))))

## df_yellow
df_yellow = df_yellow.withColumn('trip_duration', (unix_timestamp(col('tpep_dropoff_timestamp')) - unix_timestamp(col('tpep_pickup_timestamp'))))

In [0]:
# Remove trips having trip duration <= 0
df_green = df_green.filter(col('trip_duration') > 0)
df_yellow = df_yellow.filter(col('trip_duration') > 0)

In [0]:
# Calculate speed of trips
df_green = df_green.withColumn('speed', col('trip_distance')/(col('trip_duration')/3600))
df_yellow = df_yellow.withColumn('speed', col('trip_distance')/(col('trip_duration')/3600))

In [0]:
# Remove trips with negative speed
df_green = df_green.filter(col('speed') >= 0)
df_yellow = df_yellow.filter(col('speed') >= 0)

Remove trips with very high speed

In [0]:
# Set speed limit within NYC as 55km/h
speed_limit = 55

# Remove trips having speed higher than 55km/h
df_green = df_green.filter(col('speed') <= speed_limit)
df_yellow = df_yellow.filter(col('speed') <= speed_limit)

Remove trips that are travelling too short or too long (duration wise)

In [0]:
from pyspark.sql.functions import min, max

In [0]:
# Define min and max duration for a trip
min_duration = 180 # 3 minutes
max_duration = 7200 # 2 hours

# Filter too long or too short trips
df_green = df_green.filter((col('trip_duration') >= min_duration) & (col('trip_duration') <= max_duration))
df_yellow = df_yellow.filter((col('trip_duration') >= min_duration) & (col('trip_duration') <= max_duration))

Remove trips that are travelling too short or too long (distance wise)

In [0]:
# Define min and max distance for a trip
min_distance = 0.5 
max_distance = 50 

# Filter too long or too short trips
df_green = df_green.filter((col('trip_distance') >= min_distance) & (col('trip_distance') <= max_distance))
df_yellow = df_yellow.filter((col('trip_distance') >= min_distance) & (col('trip_distance') <= max_distance))

Remove trips with invalid number of passengers

In [0]:
df_green = df_green.filter((col('passenger_count') <= 5) & (col('passenger_count') > 0))
df_yellow = df_yellow.filter((col('passenger_count') <= 5) & (col('passenger_count') > 0))

In [0]:
# Check number of records after filtering
green_taxi_count = df_green.count()
yellow_taxi_count = df_yellow.count()
print(f"Green taxi: {green_taxi_count}")
print(f"Yellow taxi: {yellow_taxi_count}")

Green taxi: 57827890
Yellow taxi: 589812060


In [0]:
# Combine yellow and green taxi dataset
from pyspark.sql.functions import lit

# Drop columns
df_green = df_green.drop('ehail_fee')

# Add missing columns to 2 datasets
df_green = (df_green.withColumn('airport_fee', lit(None))
            .withColumn('taxi_color',lit('green')))

df_yellow = (df_yellow.withColumn('trip_type', lit(None))
             .withColumn('taxi_color',lit('yellow')))


# Rename lpep_pickup_datetime and lpep_dropoff_datetime in df_green 
df_green = (df_green
    .withColumnRenamed('lpep_pickup_datetime', 'tpep_pickup_datetime')
    .withColumnRenamed('lpep_dropoff_datetime', 'tpep_dropoff_datetime')
    .withColumnRenamed('lpep_pickup_timestamp', 'tpep_pickup_timestamp')
    .withColumnRenamed('lpep_dropoff_timestamp', 'tpep_dropoff_timestamp'))

In [0]:
# Merge the dataframes
data = df_yellow.unionByName(df_green)

In [0]:
data.count()

647639950

Combine the new dataframe with the location data

In [0]:
# Alias the dataframes to differentiate between pickup and dropoff joins
lookup_pu = taxi_zone_lookup.alias('lookup_pu')
lookup_do = taxi_zone_lookup.alias('lookup_do')

# Left join for pickup Location
df_with_pu = data.join(
    lookup_pu,
    data['PULocationID'] == lookup_pu['LocationID'],
    how='left'
).withColumnRenamed('Borough', 'PUBorough') \
 .withColumnRenamed('Zone', 'PUZone') \
 .withColumnRenamed('service_zone', 'PUservice_zone')

# Left join for drop-off Location
df_final = df_with_pu.join(
    lookup_do,
    df_with_pu['DOLocationID'] == lookup_do['LocationID'],
    how='left'
).withColumnRenamed('Borough', 'DOBorough') \
 .withColumnRenamed('Zone', 'DOZone') \
 .withColumnRenamed('service_zone', 'DOservice_zone')

# Drop any unnecessary columns
df_final = df_final.drop(lookup_pu['LocationID']).drop(lookup_do['LocationID'])

In [0]:
# count the final records
df_final.count()

647639950

#### Export into a parquet file

In [0]:
df_final.write.mode('overwrite').parquet('/dbfs/nyc_taxi_data.parquet')


In [0]:
# Read nyc_taxi_data.parquet
df_final = spark.read.parquet('/dbfs/nyc_taxi_data.parquet')


In [0]:
# Create a temporary view
df_final.createOrReplaceTempView('data_table')

In [0]:
table = spark.sql('SELECT * FROM data_table')

## **PART 2: Business Questions**

#### Question 1

In [0]:
%sql
SELECT
  DATE_FORMAT(tpep_pickup_datetime, 'yyyy-MM') AS year_month,
  COUNT(*) AS total_trips,
  DATE_FORMAT(tpep_pickup_datetime, 'EEEE') AS day_of_week,
  HOUR(tpep_pickup_datetime) AS hour_of_day,
  AVG(passenger_count) AS avg_passenger,
  AVG(total_amount) AS avg_total_amount,
  AVG(total_amount / passenger_count) AS avg_amount_per_passenger
FROM data_table
GROUP BY year_month, day_of_week, hour_of_day
ORDER BY year_month, total_trips DESC

year_month total_trips day_of_week hour_of_day avg_passenger avg_total_amount avg_amount_per_passenger 2015-01 157287 Friday 19 1.5325106334280647 15.098523145596491 12.567613943518635 2015-01 152044 Saturday 19 1.5889808213411907 13.72140946042661 11.140416543898507 2015-01 147997 Saturday 23 1.6077555626127558 15.241422866687769 12.290633949791301 2015-01 147771 Friday 18 1.5138626658816683 15.331735523216713 12.831006383756442 2015-01 146085 Saturday 18 1.5714686655029606 13.624205907526372 11.107389292766179 2015-01 145233 Friday 20 1.5390854695558172 14.861050381119458 12.322833925489471 2015-01 145168 Friday 22 1.585487159704618 15.379618373203392 12.531301147640267 2015-01 143237 Friday 23 1.581330242884171 15.879558633601484 12.968335024008919 2015-01 143077 Saturday 22 1.6088190275166518 14.806905372638795 11.919402688765228 2015-01 139981 Friday 21 1.55663268586451 15.104676134625588 12.436422288266728 2015-01 138089 Thursday 19 1.5040589764572123 15.139120567177883 12.765395251134525 2015-01 134565 Thursday 18 1.5051462118678705 15.361560658425075 12.943492979852584 2015-01 131801 Saturday 0 1.5820972526763832 15.94155507166797 13.006065799959313 2015-01 131542 Saturday 20 1.582703623177388 14.364021833336007 11.699890645828392 2015-01 131272 Thursday 20 1.5061170699006643 15.322964760199559 12.926395088065314 2015-01 130288 Thursday 21 1.5239776495149209 15.936710211231889 13.34828629395818 2015-01 130217 Saturday 21 1.5949069629925432 14.430731240933687 11.709531103211548 2015-01 126541 Saturday 17 1.5609723330778167 13.867726586644428 11.324725335399988 2015-01 123409 Thursday 22 1.5308688993509387 16.23152930500106 13.54326314666788 2015-01 122686 Saturday 15 1.5514321112433367 13.987043590960331 11.498984669536886 2015-01 120615 Saturday 13 1.5572275421796626 13.453925465327458 11.0419830272641 2015-01 119338 Friday 17 1.5094605238901273 15.874005178574034 13.284628183536823 2015-01 117984 Saturday 12 1.5393782207756983 13.104165225796217 10.843553830746178 2015-01 117533 Saturday 14 1.5538614686938987 13.81465767061529 11.366358547529144 2015-01 117028 Wednesday 19 1.481371979355368 14.795496804188305 12.591131454297773 2015-01 116048 Saturday 16 1.5480577002619607 13.905387081210515 11.407352687394278 2015-01 114673 Wednesday 18 1.477836979934248 15.087569349372052 12.834260908556388 2015-01 109918 Thursday 17 1.5089976164049563 15.871009661751993 13.298664965399617 2015-01 109612 Saturday 1 1.5736963106229245 15.776818505276697 12.925319508813747 2015-01 109207 Friday 14 1.4876335766022324 15.860602250776868 13.328050918593956 2015-01 108811 Sunday 0 1.6097637187416713 15.199296118961398 12.24420495476798 2015-01 108185 Wednesday 20 1.4809539215233165 14.95934075888896 12.741817386884664 2015-01 107979 Thursday 8 1.4192111429074172 14.773648116766259 12.858127671430328 2015-01 107519 Friday 15 1.4946753597038662 16.04644806964801 13.438838642473755 2015-01 106754 Saturday 11 1.525385465649999 13.198293834424577 11.000881490779642 2015-01 105610 Wednesday 21 1.4971404223084934 15.668397594928933 13.243582686300124 2015-01 104731 Friday 8 1.4250699410871661 14.981052696912109 13.002304115623485 2015-01 104658 Thursday 15 1.496101588029582 16.159706568064315 13.53435055132075 2015-01 103470 Thursday 14 1.4837054218614092 16.014683193200586 13.476086657969756 2015-01 103380 Friday 9 1.4218997871928807 14.977499419619557 13.002585164764284 2015-01 102468 Thursday 23 1.529384783542179 16.503403306402642 13.759907938740113 2015-01 100273 Thursday 9 1.4141593449881822 15.007193761034364 13.073987904686478 2015-01 99931 Wednesday 8 1.4199497653380833 14.342163993156063 12.516642296516547 2015-01 99540 Friday 12 1.4607494474583083 15.188807012259122 12.900905679458916 2015-01 99446 Friday 13 1.4801198640468194 15.180858355291045 12.82210981001421 2015-01 98600 Tuesday 18 1.4866531440162272 14.537676369169379 12.31729719404974 2015-01 96824 Wednesday 22 1.5130339585226804 15.959166425682595 13.409564722245467 2015-01 9

#### Question 2

In [0]:
# Separate the dataframe into green and yellow
green = table.filter(table.taxi_color == 'green')
yellow = table.filter(table.taxi_color == 'yellow')

In [0]:
# Create a temporary view
green.createOrReplaceTempView('green_table')
green = spark.sql('SELECT * FROM green_table')

yellow.createOrReplaceTempView('yellow_table')
yellow = spark.sql('SELECT * FROM yellow_table')

In [0]:
%sql
SELECT
    ROUND(AVG(trip_duration/60), 2) AS avg_trip_duration,
    ROUND(PERCENTILE(trip_duration/60,0.5),2) AS median_trip_duration,
    ROUND(MIN(trip_duration/60), 2) AS min_trip_duration,
    ROUND(MAX(trip_duration/60), 2) AS max_trip_duration,
    ROUND(AVG(trip_distance*1.60934), 2) AS avg_distance_km,
    ROUND(PERCENTILE(trip_distance*1.60934, 0.5), 2) AS median_distance_km,
    ROUND(MIN(trip_distance*1.60934), 2) AS min_distance_km,
    ROUND(MAX(trip_distance*1.60934), 2) AS max_distance_km,
    ROUND(AVG((trip_distance*1.60934) / (trip_duration/3600)), 2) AS avg_speed_kmph,
    ROUND(PERCENTILE((trip_distance*1.60934) / (trip_duration/3600), 0.5), 2) AS median_speed_kmph,
    ROUND(MIN((trip_distance*1.60934) / (trip_duration/3600)), 2) AS min_speed_kmph,
    ROUND(MAX((trip_distance*1.60934) / (trip_duration/3600)), 2) AS max_speed_kmph
FROM green_table

avg_trip_duration median_trip_duration min_trip_duration max_trip_duration avg_distance_km median_distance_km min_distance_km max_distance_km avg_speed_kmph median_speed_kmph min_speed_kmph max_speed_kmph 14.24 11.08 3.0 120.0 4.98 3.27 0.8 80.47 20.23 18.31 0.4 88.51

In [0]:
%sql
SELECT
    ROUND(AVG(trip_duration/60), 2) AS avg_trip_duration,
    ROUND(PERCENTILE(trip_duration/60,0.5),2) AS median_trip_duration,
    ROUND(MIN(trip_duration/60), 2) AS min_trip_duration,
    ROUND(MAX(trip_duration/60), 2) AS max_trip_duration,
    ROUND(AVG(trip_distance*1.60934), 2) AS avg_distance_km,
    ROUND(PERCENTILE(trip_distance*1.60934, 0.5), 2) AS median_distance_km,
    ROUND(MIN(trip_distance*1.60934), 2) AS min_distance_km,
    ROUND(MAX(trip_distance*1.60934), 2) AS max_distance_km,
    ROUND(AVG((trip_distance*1.60934) / (trip_duration/3600)), 2) AS avg_speed_kmph,
    ROUND(PERCENTILE((trip_distance*1.60934) / (trip_duration/3600), 0.5), 2) AS median_speed_kmph,
    ROUND(MIN((trip_distance*1.60934) / (trip_duration/3600)), 2) AS min_speed_kmph,
    ROUND(MAX((trip_distance*1.60934) / (trip_duration/3600)), 2) AS max_speed_kmph
FROM yellow_table

avg_trip_duration median_trip_duration min_trip_duration max_trip_duration avg_distance_km median_distance_km min_distance_km max_distance_km avg_speed_kmph median_speed_kmph min_speed_kmph max_speed_kmph 15.06 11.87 3.0 120.0 5.1 2.9 0.8 80.47 18.75 16.42 0.4 88.51

#### Question 3

In [0]:
%sql
SELECT
    PUBorough,
    DOBorough,
    DATE_FORMAT(tpep_pickup_datetime, 'yyyy-MM') AS year_month,
    DATE_FORMAT(tpep_pickup_datetime, 'EEEE') AS day_of_week,
    HOUR(tpep_pickup_datetime) AS hour_of_day,
    COUNT(*) AS total_trips,
    ROUND(AVG(trip_distance), 2) AS avg_distance,
    ROUND(AVG(total_amount), 2) AS avg_amount_per_trip,
    ROUND(SUM(total_amount), 2) AS total_amount_paid
FROM green_table
GROUP BY PUBorough, DOBorough, year_month, day_of_week, hour_of_day
ORDER BY PUBorough, DOBorough, year_month, day_of_week, hour_of_day


PUBorough DOBorough year_month day_of_week hour_of_day total_trips avg_distance avg_amount_per_trip total_amount_paid Bronx Bronx 2015-01 Friday 0 290 2.36 9.81 2846.11 Bronx Bronx 2015-01 Friday 1 213 2.13 9.77 2080.37 Bronx Bronx 2015-01 Friday 2 142 2.24 9.7 1376.96 Bronx Bronx 2015-01 Friday 3 88 3.48 11.81 1039.18 Bronx Bronx 2015-01 Friday 4 64 2.57 9.75 624.28 Bronx Bronx 2015-01 Friday 5 68 2.77 9.75 663.1 Bronx Bronx 2015-01 Friday 6 160 2.8 10.29 1646.16 Bronx Bronx 2015-01 Friday 7 532 2.1 10.46 5566.12 Bronx Bronx 2015-01 Friday 8 841 2.29 11.39 9578.48 Bronx Bronx 2015-01 Friday 9 590 2.24 10.61 6258.57 Bronx Bronx 2015-01 Friday 10 444 2.42 10.68 4740.13 Bronx Bronx 2015-01 Friday 11 492 2.28 10.8 5315.72 Bronx Bronx 2015-01 Friday 12 547 2.4 11.02 6027.77 Bronx Bronx 2015-01 Friday 13 536 2.39 10.85 5816.62 Bronx Bronx 2015-01 Friday 14 642 2.27 10.97 7044.1 Bronx Bronx 2015-01 Friday 15 749 2.28 11.14 8345.03 Bronx Bronx 2015-01 Friday 16 782 2.23 12.0 9380.5 Bronx Bronx 2015-01 Friday 17 814 2.28 12.36 10057.29 Bronx Bronx 2015-01 Friday 18 888 2.2 11.52 10232.1 Bronx Bronx 2015-01 Friday 19 782 2.25 11.31 8846.73 Bronx Bronx 2015-01 Friday 20 665 2.26 10.65 7082.88 Bronx Bronx 2015-01 Friday 21 548 2.44 10.77 5901.73 Bronx Bronx 2015-01 Friday 22 522 2.39 10.52 5490.06 Bronx Bronx 2015-01 Friday 23 567 2.54 10.85 6153.15 Bronx Bronx 2015-01 Monday 0 143 2.46 9.56 1367.65 Bronx Bronx 2015-01 Monday 1 116 2.56 10.1 1172.03 Bronx Bronx 2015-01 Monday 2 75 2.78 10.1 757.8 Bronx Bronx 2015-01 Monday 3 43 2.32 9.48 407.8 Bronx Bronx 2015-01 Monday 4 53 2.77 10.34 548.2 Bronx Bronx 2015-01 Monday 5 36 2.87 10.96 394.7 Bronx Bronx 2015-01 Monday 6 98 3.36 10.27 1005.99 Bronx Bronx 2015-01 Monday 7 390 2.19 10.23 3988.54 Bronx Bronx 2015-01 Monday 8 550 2.2 10.25 5638.09 Bronx Bronx 2015-01 Monday 9 383 2.39 10.74 4114.17 Bronx Bronx 2015-01 Monday 10 341 2.45 10.78 3675.39 Bronx Bronx 2015-01 Monday 11 310 2.32 10.42 3229.43 Bronx Bronx 2015-01 Monday 12 322 2.33 10.66 3433.37 Bronx Bronx 2015-01 Monday 13 404 2.22 10.44 4216.48 Bronx Bronx 2015-01 Monday 14 423 2.43 11.44 4838.23 Bronx Bronx 2015-01 Monday 15 441 2.31 11.55 5092.77 Bronx Bronx 2015-01 Monday 16 433 2.32 11.95 5174.15 Bronx Bronx 2015-01 Monday 17 417 2.18 11.23 4681.93 Bronx Bronx 2015-01 Monday 18 319 2.3 11.53 3678.35 Bronx Bronx 2015-01 Monday 19 279 2.3 11.07 3087.97 Bronx Bronx 2015-01 Monday 20 231 2.58 11.33 2616.42 Bronx Bronx 2015-01 Monday 21 206 2.22 10.05 2069.32 Bronx Bronx 2015-01 Monday 22 156 2.49 11.02 1719.9 Bronx Bronx 2015-01 Monday 23 171 2.36 9.68 1654.55 Bronx Bronx 2015-01 Saturday 0 497 2.37 10.67 5302.2 Bronx Bronx 2015-01 Saturday 1 371 2.44 10.73 3980.64 Bronx Bronx 2015-01 Saturday 2 304 2.65 11.02 3348.76 Bronx Bronx 2015-01 Saturday 3 228 2.81 11.77 2684.31 Bronx Bronx 2015-01 Saturday 4 217 3.11 12.59 2731.18 Bronx Bronx 2015-01 Saturday 5 125 3.16 12.17 1521.01 Bronx Bronx 2015-01 Saturday 6 110 2.85 11.1 1220.6 Bronx Bronx 2015-01 Saturday 7 210 2.59 10.53 2210.72 Bronx Bronx 2015-01 Saturday 8 293 2.45 10.25 3004.49 Bronx Bronx 2015-01 Saturday 9 360 2.37 10.02 3605.93 Bronx Bronx 2015-01 Saturday 10 346 2.4 10.73 3711.16 Bronx Bronx 2015-01 Saturday 11 359 2.23 10.1 3627.52 Bronx Bronx 2015-01 Saturday 12 357 2.12 10.17 3631.92 Bronx Bronx 2015-01 Saturday 13 404 2.39 11.05 4464.39 Bronx Bronx 2015-01 Saturday 14 432 2.34 11.03 4763.71 Bronx Bronx 2015-01 Saturday 15 496 2.41 11.07 5490.26 Bronx Bronx 2015-01 Saturday 16 524 2.27 10.48 5493.69 Bronx Bronx 2015-01 Saturday 17 658 2.4 10.95 7203.7 Bronx Bronx 2015-01 Saturday 18 627 2.25 10.24 6418.4 Bronx Bronx 2015-01 Saturday 19 607 2.45 11.23 6817.52 Bronx Bronx 2015-01 Saturday 20 532 2.32 10.84 5764.83 Bronx Bronx 2015-01 Saturday 21 498 2.51 11.6 5778.36 Bronx Bronx 2015-01 Saturday 22 475 2.46 10.81 5135.26 Bronx Bronx 2015-01 Saturday 23 531 2.5 10.97 5823.96 Bronx Bronx 2015-01 Sunday 0 365 2.48 10.55 3849.98 Bronx Bronx 2015-01 Sunday 1 292 2.55 11.04 322

In [0]:
%sql
SELECT
    PUBorough,
    DOBorough,
    DATE_FORMAT(tpep_pickup_datetime, 'yyyy-MM') AS year_month,
    DATE_FORMAT(tpep_pickup_datetime, 'EEEE') AS day_of_week,
    HOUR(tpep_pickup_datetime) AS hour_of_day,
    COUNT(*) AS total_trips,
    ROUND(AVG(trip_distance), 2) AS avg_distance,
    ROUND(AVG(total_amount), 2) AS avg_amount_per_trip,
    ROUND(SUM(total_amount), 2) AS total_amount_paid
FROM yellow_table
GROUP BY PUBorough, DOBorough, year_month, day_of_week, hour_of_day
ORDER BY PUBorough, DOBorough, year_month, day_of_week, hour_of_day

PUBorough DOBorough year_month day_of_week hour_of_day total_trips avg_distance avg_amount_per_trip total_amount_paid Bronx Bronx 2015-01 Friday 0 39 3.32 14.33 558.94 Bronx Bronx 2015-01 Friday 1 28 3.09 13.71 384.01 Bronx Bronx 2015-01 Friday 2 29 2.91 12.95 375.64 Bronx Bronx 2015-01 Friday 3 26 2.4 11.82 307.38 Bronx Bronx 2015-01 Friday 4 29 2.77 12.45 360.92 Bronx Bronx 2015-01 Friday 5 18 2.89 12.68 228.3 Bronx Bronx 2015-01 Friday 6 32 2.33 10.4 332.85 Bronx Bronx 2015-01 Friday 7 51 2.16 11.92 608.13 Bronx Bronx 2015-01 Friday 8 55 2.08 12.01 660.32 Bronx Bronx 2015-01 Friday 9 20 2.28 12.99 259.81 Bronx Bronx 2015-01 Friday 10 14 1.51 10.31 144.3 Bronx Bronx 2015-01 Friday 11 11 3.62 17.12 188.33 Bronx Bronx 2015-01 Friday 12 21 2.47 12.68 266.37 Bronx Bronx 2015-01 Friday 13 20 2.94 14.08 281.61 Bronx Bronx 2015-01 Friday 14 21 2.09 10.74 225.5 Bronx Bronx 2015-01 Friday 15 20 1.87 10.69 213.76 Bronx Bronx 2015-01 Friday 16 8 2.87 15.7 125.56 Bronx Bronx 2015-01 Friday 17 27 2.47 13.89 375.1 Bronx Bronx 2015-01 Friday 18 37 2.15 12.9 477.39 Bronx Bronx 2015-01 Friday 19 31 2.06 12.85 398.36 Bronx Bronx 2015-01 Friday 20 33 2.5 12.87 424.8 Bronx Bronx 2015-01 Friday 21 26 2.11 11.0 286.13 Bronx Bronx 2015-01 Friday 22 31 2.6 12.05 373.4 Bronx Bronx 2015-01 Friday 23 45 2.58 12.19 548.72 Bronx Bronx 2015-01 Monday 0 30 2.76 12.63 378.87 Bronx Bronx 2015-01 Monday 1 24 3.48 14.22 341.2 Bronx Bronx 2015-01 Monday 2 17 3.16 14.77 251.09 Bronx Bronx 2015-01 Monday 3 16 3.52 15.09 241.45 Bronx Bronx 2015-01 Monday 4 17 4.21 19.19 326.25 Bronx Bronx 2015-01 Monday 5 8 3.49 14.19 113.55 Bronx Bronx 2015-01 Monday 6 26 2.74 12.4 322.4 Bronx Bronx 2015-01 Monday 7 25 2.08 10.9 272.54 Bronx Bronx 2015-01 Monday 8 23 1.78 10.44 240.14 Bronx Bronx 2015-01 Monday 9 12 2.18 10.67 128.06 Bronx Bronx 2015-01 Monday 10 3 1.49 8.8 26.4 Bronx Bronx 2015-01 Monday 11 9 2.35 10.89 98.0 Bronx Bronx 2015-01 Monday 12 13 1.99 10.29 133.78 Bronx Bronx 2015-01 Monday 13 12 2.39 13.69 164.29 Bronx Bronx 2015-01 Monday 14 19 1.92 41.22 783.15 Bronx Bronx 2015-01 Monday 15 16 2.33 15.85 253.56 Bronx Bronx 2015-01 Monday 16 18 2.24 13.25 238.43 Bronx Bronx 2015-01 Monday 17 9 2.4 12.36 111.2 Bronx Bronx 2015-01 Monday 18 19 3.09 14.49 275.38 Bronx Bronx 2015-01 Monday 19 8 2.26 15.71 125.66 Bronx Bronx 2015-01 Monday 20 21 3.01 13.13 275.67 Bronx Bronx 2015-01 Monday 21 10 2.43 11.37 113.7 Bronx Bronx 2015-01 Monday 22 14 2.62 12.26 171.65 Bronx Bronx 2015-01 Monday 23 19 3.04 13.29 252.6 Bronx Bronx 2015-01 Saturday 0 47 3.03 13.69 643.62 Bronx Bronx 2015-01 Saturday 1 66 2.93 13.12 865.99 Bronx Bronx 2015-01 Saturday 2 91 3.16 13.62 1239.58 Bronx Bronx 2015-01 Saturday 3 86 3.96 17.81 1531.39 Bronx Bronx 2015-01 Saturday 4 70 3.19 14.4 1008.18 Bronx Bronx 2015-01 Saturday 5 31 3.29 14.08 436.62 Bronx Bronx 2015-01 Saturday 6 29 3.14 13.83 401.11 Bronx Bronx 2015-01 Saturday 7 35 3.29 13.06 457.23 Bronx Bronx 2015-01 Saturday 8 45 3.05 12.68 570.75 Bronx Bronx 2015-01 Saturday 9 34 2.16 10.4 353.55 Bronx Bronx 2015-01 Saturday 10 15 1.94 10.96 164.45 Bronx Bronx 2015-01 Saturday 11 12 1.66 10.32 123.79 Bronx Bronx 2015-01 Saturday 12 22 2.94 13.29 292.45 Bronx Bronx 2015-01 Saturday 13 14 2.03 10.79 151.0 Bronx Bronx 2015-01 Saturday 14 13 3.21 15.21 197.76 Bronx Bronx 2015-01 Saturday 15 23 2.74 13.48 309.93 Bronx Bronx 2015-01 Saturday 16 24 2.49 12.16 291.89 Bronx Bronx 2015-01 Saturday 17 36 2.61 13.36 480.87 Bronx Bronx 2015-01 Saturday 18 39 2.19 11.88 463.4 Bronx Bronx 2015-01 Saturday 19 37 2.39 12.73 471.06 Bronx Bronx 2015-01 Saturday 20 33 2.26 12.09 398.86 Bronx Bronx 2015-01 Saturday 21 29 2.48 12.45 361.18 Bronx Bronx 2015-01 Saturday 22 40 2.98 13.89 555.47 Bronx Bronx 2015-01 Saturday 23 45 3.07 13.92 626.54 Bronx Bronx 2015-01 Sunday 0 36 1.97 10.45 376.18 Bronx Bronx 2015-01 Sunday 1 46 3.47 14.9 685.49 Bronx Bronx 2015-01 Sunday 2 40 3.22 14.02 560.97 Bronx Bronx 2015-01 Sunday 3 36 3.26 13.76 495.18 Bronx Bronx 2015-01 Sunday 

#### Question 4

In [0]:
%sql
SELECT (COUNT(CASE WHEN tip_amount > 0 THEN 1 END) * 100 / COUNT(*)) AS percentage_trips_with_tips
FROM data_table;

percentage_trips_with_tips 64.41972580598217

#### Question 5

In [0]:
%sql
SELECT (COUNT(CASE WHEN tip_amount >= 5 THEN 1 END) * 100 / COUNT(*)) AS percentage_trips_with_tips_at_least_5_dollars
FROM data_table;

percentage_trips_with_tips_at_least_5_dollars 8.210529168251588

#### Question 6

In [0]:
%sql
WITH trip_statistics AS (
    SELECT
        CASE
            WHEN trip_duration < 300 THEN 'Under 5 Mins'
            WHEN trip_duration >= 300 AND trip_duration < 600 THEN 'From 5 mins to 10 mins'
            WHEN trip_duration >= 600 AND trip_duration < 1200 THEN 'From 10 mins to 20 mins'
            WHEN trip_duration >= 1200 AND trip_duration < 1800 THEN 'From 20 mins to 30 mins'
            WHEN trip_duration >= 1800 AND trip_duration < 3600 THEN 'From 30 mins to 60 mins'
            ELSE 'At least 60 mins'
        END AS duration_bin,
        (trip_distance * 1.60934) / (trip_duration / 3600) AS speed,
        (trip_distance * 1.60934) / total_amount AS distance_per_dollar,
        tip_amount
    FROM data_table
    WHERE trip_duration > 0
)

SELECT
    duration_bin,
    ROUND((SUM(CASE WHEN tip_amount > 0 THEN 1 ELSE 0 END) * 100 / COUNT(*)), 4) AS percentage_trips_with_tips,
    ROUND((SUM(CASE WHEN tip_amount >= 5 THEN 1 ELSE 0 END) * 100 / SUM(CASE WHEN tip_amount > 0 THEN 1 ELSE 0 END)), 4) AS percentage_trips_with_tips_at_least_5_dollars,
    ROUND(AVG(speed), 2) AS avg_speed_kmph,
    ROUND(AVG(distance_per_dollar), 2) AS avg_distance_per_dollar_kmpd
FROM trip_statistics
GROUP BY duration_bin;

duration_bin percentage_trips_with_tips percentage_trips_with_tips_at_least_5_dollars avg_speed_kmph avg_distance_per_dollar_kmpd From 5 mins to 10 mins 62.9163 0.4501 17.21 0.21 Under 5 Mins 59.2211 0.3822 19.69 0.18 From 10 mins to 20 mins 65.9989 3.9366 17.71 0.26 From 20 mins to 30 mins 66.6003 29.584 21.16 0.31 At least 60 mins 58.9663 94.8876 22.74 0.5 From 30 mins to 60 mins 66.052 76.348 25.62 0.37

#### Question 7

In [0]:
%sql
WITH trip_statistics AS (
    SELECT
        CASE
            WHEN trip_duration < 300 THEN 'Under 5 Mins'
            WHEN trip_duration >= 300 AND trip_duration < 600 THEN 'From 5 mins to 10 mins'
            WHEN trip_duration >= 600 AND trip_duration < 1200 THEN 'From 10 mins to 20 mins'
            WHEN trip_duration >= 1200 AND trip_duration < 1800 THEN 'From 20 mins to 30 mins'
            WHEN trip_duration >= 1800 AND trip_duration < 3600 THEN 'From 30 mins to 60 mins'
            ELSE 'At least 60 mins'
        END AS duration_bin,
        (trip_distance * 1.60934) / (trip_duration / 3600) AS speed,
        (trip_distance * 1.60934) / total_amount AS distance_per_dollar,
        tip_amount,
        total_amount, trip_duration
    FROM data_table
    WHERE trip_duration > 0
)
SELECT
    duration_bin,
    SUM(total_amount) AS total_income,
    SUM(trip_duration)/3600 AS total_trip_hours,
    SUM(total_amount) / (SUM(trip_duration)/3600) AS avg_income_per_hours
FROM trip_statistics
GROUP BY duration_bin

duration_bin total_income total_trip_hours avg_income_per_hours From 5 mins to 10 mins 2.0171733489330919E9 2.494501306611111E7 80.86479424111867 Under 5 Mins 4.702643530107109E8 4219329.1605555555 111.45476807237091 From 10 mins to 20 mins 3.7888335004585156E9 5.7032258425E7 66.43316616053357 From 20 mins to 30 mins 2.3162684780617347E9 3.510888425861111E7 65.97385610434563 At least 60 mins 3.8385215952006483E8 6903671.509722223 55.60116221918988 From 30 mins to 60 mins 2.32635530949347E9 3.3539491726944443E7 69.36167454274683

## **PART 3: Machine Learning**

In [0]:
# Import Spark Session
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, avg, round, when, count
from pyspark.ml import Pipeline

# Import VectorAssembler to combine multiple columns into a single feature vector
# Import StringIndexer to index categorical columns 
from pyspark.ml.feature import VectorAssembler

# Import data types for defining schema 
from pyspark.sql.types import IntegerType, DoubleType

# Calculate RMSE for the baseline model
from pyspark.ml.evaluation import RegressionEvaluator 

# Import models
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.regression import LinearRegression

In [0]:
# Create a Spark Session
data_processing_spark = SparkSession.builder.appName('Total_amount_prediction').getOrCreate()

In [0]:
list_columns = ['passenger_count', 'trip_distance', 'extra', 'mta_tax', 'tip_amount', 
                'improvement_surcharge', 'total_amount', 'congestion_surcharge', 
                'airport_fee', 'trip_duration', 'speed', 'taxi_color']
df_new = df_final.select(list_columns)

In [0]:
# Convert data types
df_new = df_new.withColumn('trip_duration', col('trip_duration').cast(DoubleType()))
df_new = df_new.withColumn('passenger_count', col('passenger_count').cast(IntegerType()))

In [0]:
# Handle null values
# check for null or specific 'N' values
null_summary = []

for column_name in df_new.columns:
    count_null = df_new.filter((col(column_name).isNull()) | (col(column_name) == 'N')).count()
    if count_null > 0:
        null_summary.append((column_name, count_null))

# Convert summary to a DataFrame for better visibility
null_df = spark.createDataFrame(null_summary, ["Column Name", "Null Count"])
display(null_df)

Column Name Null Count improvement_surcharge 4 congestion_surcharge 488552331 airport_fee 590169639

In [0]:
# Initialize Spark session
spark = SparkSession.builder \
    .appName("Data Imputation") \
    .getOrCreate()

# Initialize the Imputer
imputer = Imputer(inputCols=null_cols, outputCols=[f"{col}_imputed" for col in null_cols], strategy='mean')
imputer_model = imputer.fit(df_new)

# Transform the DataFrame to impute missing values
df_imputed = imputer_model.transform(df_new)

# Check for null values after imputation
null_summary = []

for column_name in df_imputed.columns:
    count_null = df_imputed.filter(col(column_name).isNull()).count()
    if count_null > 0:
        null_summary.append((column_name, count_null))

# Convert summary to a DataFrame for better visibility
null_df = spark.createDataFrame(null_summary, ["Column Name", "Null Count"])
display(null_df)

# Remove rows with null values in the imputed columns if necessary
df_cleaned = df_imputed.dropna(subset=null_cols)

# Show the cleaned DataFrame
df_cleaned.show(truncate=False)

Column Name Null Count improvement_surcharge 4 congestion_surcharge 488552331 airport_fee 590169639

+---------------+-------------+-----+-------+----------+---------------------+------------+--------------------+-----------+-------------+------------------+----------+----------------------------+---------------------------+------------------+-----------------------------+----------------------------+-------------------+
|passenger_count|trip_distance|extra|mta_tax|tip_amount|improvement_surcharge|total_amount|congestion_surcharge|airport_fee|trip_duration|speed             |taxi_color|improvement_surcharge_impute|congestion_surcharge_impute|airport_fee_impute|improvement_surcharge_imputed|congestion_surcharge_imputed|airport_fee_imputed|
+---------------+-------------+-----+-------+----------+---------------------+------------+--------------------+-----------+-------------+------------------+----------+----------------------------+---------------------------+------------------+-----------------------------+----------------------------+-------------------+
|1              |2.1        

In [0]:
# Import Imputer  to impute missing values in numerical columns
from pyspark.ml.feature import Imputer

# Define the columns with null values
null_cols = ['improvement_surcharge', 'congestion_surcharge', 'airport_fee']

imputer = Imputer(inputCols=null_cols, outputCols=[f"{col}_imputed" for col in null_cols], strategy='mean')
imputer_model = imputer.fit(df_new)

# Transform the DataFrame to impute missing values
df_new = imputer_model.transform(df_new)

#### Feature selection

In [0]:
selected_features = ['passenger_count', 'trip_distance', 'extra', 'mta_tax', 'tip_amount',
               'improvement_surcharge', 'congestion_surcharge', 'airport_fee', 'trip_duration', 'speed']
target_feature = 'total_amount'

In [0]:
# VectorAssembler to combine features into a single vector
assembler = VectorAssembler(
    inputCols=selected_features,
    outputCol="features"
)

In [0]:
final_data = assembler.transform(df_cleaned)

In [0]:
final_data.write.mode('overwrite').parquet('/dbfs/final_data.parquet')

In [0]:
# Splitting
# Train and validation: all data except October, November, December 2022
train_validation = final_data.filter(col('tpep_pickup_datetime') < '2022-10-01')

# Testset: October, November, and December 2022
test = final_data.filter(col('tpep_pickup_datetime') >= '2022-10-01')

In [0]:
# Split the dataset into training and validation sets
(train, validation) = train_validation.randomSplit([0.8, 0.2], seed=42)

#### Baseline model

In [0]:
# Calculate the average amount per trip for each taxi color
avg_amount = df_final.groupBy('taxi_color').agg(round(avg('total_amount'), 2).alias('avg_amount_per_trip'))
display(avg_amount)

taxi_color avg_amount_per_trip green 15.5 yellow 17.64

In [0]:
# Join with the train DataFrame to add the baseline prediction to each trip
df_with_baseline_train = train_validation.join(avg_amount, on='taxi_color', how='left')

# Baseline prediction: use the average amount per trip for each taxi color in the training DataFrame
df_with_baseline_train = df_with_baseline_train.withColumn('baseline_prediction', col('avg_amount_per_trip'))

df_with_baseline_validation = test.join(avg_amount, on='taxi_color', how='left')

# Baseline prediction
df_with_baseline_validation = df_with_baseline_validation.withColumn('baseline_prediction', col('avg_amount_per_trip'))

# Calculate RMSE for the baseline model on the validation set
baseline_evaluator = RegressionEvaluator(labelCol='total_amount', predictionCol='baseline_prediction', metricName='rmse')
baseline_rmse = baseline_evaluator.evaluate(df_with_baseline_validation)
print(f"Baseline Model RMSE: {baseline_rmse}")

Baseline Model RMSE: 18.79564997547481


#### Model development

In [0]:
# Linear Regression
linear = LinearRegression(featuresCol="features", labelCol=target_feature)

# Fitting model on the train data
lreg_model = linear.fit(train)

In [0]:
# Random Forest
randomforest = RandomForestRegressor(featuresCol="features", labelCol=target_feature)

# Fitting model on the train data
rf_model = randomforest.fit(train)

In [0]:
# Making prediction 
linear_predictions = lreg_model.transform(test)
randomforest_predictions = rf_model.transform(test)

# Define evaluator
evaluator = RegressionEvaluator(labelCol=target_feature, predictionCol="prediction", metricName="rmse")

# Calculate RMSE score of linear regression and random forest
rmse1 = evaluator.evaluate(linear_predictions)
rmse2 = evaluator.evaluate(randomforest_predictions)

In [0]:
rmse1

30.53241184778551

In [0]:
rmse2

5.5626999918609865